In [81]:
# using GuSTO
include("../src/GuSTO.jl")
using Plots

  likely near /home/acauligi/.julia/dev/GuSTO/src/GuSTO.jl:19


In [82]:
robot = PandaBot()
env = Factory()

push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,-0.25,0.30), Vec3f0(.3,0.5,0.01)))
push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,-0.25,0.62), Vec3f0(.3,0.5,0.01)))

push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,-0.26,0.30), Vec3f0(.3,0.01,0.33)))
push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,0.25,0.30), Vec3f0(.3,0.01,0.33)))

th_init = [0;  -0.6; 0.; 1.20*pi; 0.25; 1.10*pi; 0.25*pi+0.001]
th_goal = [0;  +0.1; 0.; 1.20*pi; 0.25; 1.42*pi; 0.25*pi-0.001]

7-element Array{Float64,1}:
 0.0               
 0.1               
 0.0               
 3.7699111843077517
 0.25              
 4.461061568097506 
 0.7843981633974483

In [83]:
robot = PandaBot()
env = Factory()
#push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,0.1,0.), Vec3f0(.2,0.2,0.3)))
push!(env.obstacle_set, HyperRectangle(Vec3f0(0.45,-0.2,0.), Vec3f0(.2,0.2,0.3)))

th_init = [pi/4;  0.50; 0; -0.5*pi; 0.25;  0.5*pi; 0.25*pi-0.001]
th_goal = [-pi/5; 0.65; 0; -0.5*pi; 0.25;  0.5*pi; 0.25*pi+0.001]

7-element Array{Float64,1}:
 -0.6283185307179586
  0.65              
  0.0               
 -1.5707963267948966
  0.25              
  1.5707963267948966
  0.7863981633974483

In [84]:
pan = Panda()

state = RigidBodyDynamics.MechanismState(pan.mechanism)
world_frame = RigidBodyDynamics.root_frame(pan.mechanism)

set_configuration!(state,th_goal)

EE_id = 7 + 2
EE_link = RigidBodyDynamics.bodies(pan.mechanism)[EE_id]
EE_link_frame = RigidBodyDynamics.default_frame(EE_link)
EE_link_point = RigidBodyDynamics.Point3D(EE_link_frame, 0.0,0.0,0.)
p_EE = RigidBodyDynamics.Spatial.transform(state,EE_link_point,world_frame)
p_EE.v

world_frame = RigidBodyDynamics.root_frame(pan.mechanism)
EE_path = RigidBodyDynamics.path(pan.mechanism, root_body(pan.mechanism), EE_link)
J_pEE_joint = point_jacobian(state,EE_path, RigidBodyDynamics.Spatial.transform(state,EE_link_point,world_frame))
J_pEE_joint.J[:,1:robot.num_joints];

In [85]:
model = PandaKin()

x_init, x_goal = zeros(model.x_dim), zeros(model.x_dim)
for i in 1:robot.num_joints
    x_init[2*i-1:2*i] = [cos(th_init[i]); sin(th_init[i])]
    x_goal[2*i-1:2*i] = [cos(th_goal[i]); sin(th_goal[i])]
end

r_EE_inWorldFrame = get_EE_position(x_goal,robot)
model.p_EE_goal = r_EE_inWorldFrame

N = 31
tf_guess = 100.

100.0

In [86]:
PD = ProblemDefinition(robot, model, env, x_init, x_goal);
TOP = TrajectoryOptimizationProblem(PD, N, tf_guess, fixed_final_time=true)
TOS_SCP = TrajectoryOptimizationSolution(TOP)

solve_SCP!(TOS_SCP, TOP, solve_gusto_jump!, init_traj_so1, "Gurobi")

Academic license - for non-commercial use only
Warning, invalid warm-start basis discarded
Warning, invalid warm-start basis discarded
Warning, invalid warm-start basis discarded
Warning for adding constraints: zero or small (< 1e-13) coefficients, ignored
Optimize a model with 967 rows, 924 columns and 3137 nonzeros
Model has 211 quadratic objective terms
Model has 31 quadratic constraints
Coefficient statistics:
  Matrix range     [2e-13, 1e+02]
  QMatrix range    [1e+01, 1e+01]
  QLMatrix range   [4e-01, 2e+01]
  Objective range  [1e+00, 1e+00]
  QObjective range [2e+00, 2e+00]
  Bounds range     [1e+02, 1e+02]
  RHS range        [6e-17, 4e+01]
  QRHS range       [7e+01, 7e+01]
Presolve removed 545 rows and 264 columns
Presolve time: 0.00s
Presolved: 483 rows, 725 columns, 2410 nonzeros
Presolved model has 31 second-order cone constraints
Ordering time: 0.00s

Barrier statistics:
 Dense cols : 1
 AA' NZ     : 9.094e+03
 Factor NZ  : 9.721e+03 (roughly 1 MByte of memory)
 Factor Ops 

In [87]:
# TOS_SCPS  = TrajectoryOptimizationSolution(TOP)
# solve_SCPshooting!(TOS_SCPS, TOP, solve_gusto_jump!, init_traj_so1, "Ipopt", print_level=0)

In [88]:
@show TOS_SCP.SCPS.converged
@show TOS_SCP.SCPS.successful
@show TOS_SCP.SCPS.iterations
@show TOS_SCP.SCPS.total_time
@show TOS_SCP.SCPS.accept_solution
@show TOS_SCP.SCPS.prob_status
@show TOS_SCP.SCPS.convergence_measure
@show TOS_SCP.SCPS.param.alg.ω_vec
@show TOS_SCP.SCPS.param.alg.Δ_vec
@show TOS_SCP.SCPS.J_true[end];

(TOS_SCP.SCPS).converged = true
(TOS_SCP.SCPS).successful = true
(TOS_SCP.SCPS).iterations = 15
(TOS_SCP.SCPS).total_time = 3.2355109559999993
(TOS_SCP.SCPS).accept_solution = Bool[true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true]
(TOS_SCP.SCPS).prob_status = Union{TerminationStatusCode, Symbol}[:NA, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL, OPTIMAL]
(TOS_SCP.SCPS).convergence_measure = [0.0, 0.116176, 0.11902, 0.119523, 0.0870442, 0.0444968, 0.0140262, 0.00713489, 0.00254505, 0.00140394, 0.000538992, 0.000440578, 0.000149868, 0.000214827, 0.000183187, 0.000393953]
(((TOS_SCP.SCPS).param).alg).ω_vec = [10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0]
(((TOS_SCP.SCPS).param).alg).Δ_vec = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]
(TOS_SCP.SCPS).J_true[end] = 10000.00507600921

In [89]:
r_EE_f = get_EE_position(TOS_SCP.traj.X[:,end],robot)
println("Distance between r_EE_goal and solution is ", norm(r_EE_f-r_EE_inWorldFrame))
abs.(r_EE_f-r_EE_inWorldFrame)
[r_EE_f r_EE_inWorldFrame]

Distance between r_EE_goal and solution is 0.03463387660505925


3×2 Array{Float64,2}:
  0.497036   0.517032
 -0.362916  -0.342924
  0.25213    0.232131

In [90]:
joint_traj = zeros(robot.num_joints,N)
for k in 1:N
    joint_traj[:,k] = get_configuration(TOS_SCP.traj.X[:,k],model)
end
verify_joint_limits(TOS_SCP.SCPS.traj, TOS_SCP.SCPS.SCPP)

true

In [91]:
# for idx in 1:model.num_joints
#     plot(joint_traj[idx,:], linestyle="--", color="k")
#     plot(robot.q_max[idx]*ones(N), linestyle="-.", color="r")
#     plot(robot.q_min[idx]*ones(N), linestyle="-.", color="r")
# end

In [92]:
using MeshCat
using MeshCatMechanisms

using RigidBodySim
using RigidBodyDynamics

vis = Visualizer()

pd = robot.pan
mvis = MechanismVisualizer(
    pd.mechanism,
    URDFVisuals(PandaRobot.urdfpath(), package_path=[dirname(dirname(PandaRobot.urdfpath()))]),
    vis);
# 
vis[:obstacles]
for (idx,obs) in enumerate(env.obstacle_set)
    setobject!(vis[:obstacles][Symbol(string("obs",idx))], 
        Object(obs,MeshBasicMaterial(color=RGBA(0.,0.,0.,0.5))))
end

EE_box = HyperRectangle(Vec3f0(model.p_EE_goal.-model.p_EE_goal_delta_error), Vec3f0(2*model.p_EE_goal_delta_error*ones(3)))
setobject!(vis[:obstacles][Symbol(string("obs",length(env.obstacle_set)+1))], 
        Object(EE_box,MeshBasicMaterial(color=RGBA(1.,1.,1.,0.5))))

q = Vector{Array{Float64,1}}(undef,0)
for k in 1:N
    push!(q, joint_traj[:,k]) 
end

setanimation!(mvis, 1:length(q), q)

plot_in_cell = true
plot_in_cell ? IJuliaCell(vis) : open(vis)
#sleep(1)

Scope("scope-2f8009f4-cc8a-4a8b-a81a-37d14a0fa6b3", Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{DOM}(DOM(:html, :iframe), Any[], Dict{Symbol,Any}(:attributes=>Dict{String,Any}("height"=>"100%","scrolling"=>"no","src"=>"javascript:void(0)","frameborder"=>0),:id=>"ifr",:style=>Dict("width"=>"100%","flexGrow"=>"1")), 0)], Dict{Symbol,Any}(:style=>Dict("flexDirection"=>"column","height"=>"100%","minHeight"=>"400px","display"=>"flex","width"=>"100%","overflow"=>"hidden")), 1), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}(), Set(String[]), nothing, Any[], Dict{Any,Any}("_promises"=>Dict{Any,Any}("importsLoaded"=>Any[JSString("function () {\n    var frame = this.dom.querySelector(\"#ifr\");\n    var doc = frame.contentDocument\n    var win = frame.contentWindow\n\n    // Ensure that the iframe's baseURI matches the baseURI of the\n    // outer document. This is necessary to resolve\n    // https://github.com/JuliaGizmos/WebIO.jl/issues/167\n    var base = doc.createElement(\"base\");\n    base.setAttribute(\"href\", document.baseURI);\n    doc.head.appendChild(base);\n\n    var webio = doc.createElement(\"script\")\n    webio.src = \"/assetserver/b126c1c6686658253b9d2e8db68e5b485b23159d-assets/webio/dist/bundle.js\"\n    var parent = window\n\n    function resizeIframe() {\n        doc.body.style.padding = '0'\n        doc.body.style.margin = '0'\n        doc.documentElement.height = '100%'\n        doc.body.height = '100%'\n    }\n\n    webio.onload = function () {\n        win.WebIO.sendCallback = parent.WebIO.sendCallback; // Share stuff\n        win.WebIO.scopes = parent.WebIO.scopes\n        win.WebIO.obsscopes = parent.WebIO.obsscopes\n        win.WebIO._connected = true\n        doc.body.innerHTML = \"<html><body>\" + \"<div class='display:none'></div><unsafe-script style='display:none'>\\nWebIO.mount(this.previousSibling,{&quot;props&quot;:{},&quot;nodeType&quot;:&quot;Scope&quot;,&quot;type&quot;:&quot;node&quot;,&quot;instanceArgs&quot;:{&quot;imports&quot;:{&quot;data&quot;:[{&quot;name&quot;:null,&quot;type&quot;:&quot;js&quot;,&quot;url&quot;:&quot;/assetserver/f333cf24ad96cf1690b3224dd5a2bc02eddf4714-main.min.js&quot;}],&quot;type&quot;:&quot;async_block&quot;},&quot;id&quot;:&quot;scope-778b754e-511e-4b24-adbe-9d7655ed69b9&quot;,&quot;handlers&quot;:{&quot;meshcat-command&quot;:[(function (val){return this.viewer.handle_command_message({&quot;data&quot;:val})})],&quot;_promises&quot;:{&quot;importsLoaded&quot;:[(function (mc){var element=this.dom.children[0]; this.viewer=new mc.Viewer(element); WebIO.setval({&quot;name&quot;:&quot;meshcat-request&quot;,&quot;scope&quot;:&quot;scope-778b754e-511e-4b24-adbe-9d7655ed69b9&quot;,&quot;id&quot;:&quot;ob_26&quot;,&quot;type&quot;:&quot;observable&quot;},String(Date.now())); window.document.body.style.margin=&quot;0&quot;; return window.meshcat_viewer=this.viewer})]}},&quot;systemjs_options&quot;:null,&quot;observables&quot;:{&quot;meshcat-command&quot;:{&quot;sync&quot;:false,&quot;id&quot;:&quot;ob_25&quot;,&quot;value&quot;:[131,167,111,112,116,105,111,110,115,130,164,112,108,97,121,195,171,114,101,112,101,116,105,116,105,111,110,115,1,170,97,110,105,109,97,116,105,111,110,115,156,130,164,99,108,105,112,131,164,110,97,109,101,167,100,101,102,97,117,108,116,163,102,112,115,30,166,116,114,97,99,107,115,146,131,164,110,97,109,101,169,46,112,111,115,105,116,105,111,110,164,107,101,121,115,220,3,133,130,164,116,105,109,101,0,165,118,97,108,117,101,147,203,0,0,0,0,0,0,0,0,203,191,212,57,88,16,98,77,213,203,188,105,38,23,177,76,0,0,130,164,116,105,109,101,1,165,118,97,108,117,101,147,203,0,0,0,0,0,0,0,0,203,191,212,57,88,16,98,77,210,203,188,105,111,91,163,36,0,0,130,164,116,105,109,101,2,165,118,97,108,117,101,147,203,188,144,0,0,0,0,0,0,203,191,212,57,88,16,98,77,212,203,188,105,207,79,92,200,0,0,130,164,116,105,109,101,3,165,118,97,108,117,101,147,203,188,128,0,0,0,0,0,0,203,191,212,57,88,16,98,77,212,203,60,114,221,6,76,158,0,0,130,164,116,105,1